# Setup

In [1]:
%load_ext autoreload
%autoreload 2

import glob
import os
import pandas as pd
import utilities_MAURICE as um

In [2]:
# set the cwd
cwd = "C:/Users/user/OneDrive - Politecnico di Milano/hydrogeo-modelling/Progetti/MAURICE/MAURICE_progetto/Dati/Misure_in_continuo"

In [3]:
#define diver depth and reference quote
ref = pd.DataFrame([['Pz1_diver', 15, 146.26],
                    ['Pz2_diver', 15, 128.68],
                    ['Pz3_diver', 15, 132.98],
                    ['Pz4_diver', 15, 128.68]], columns=['id_punto', 'prof_diver', 'quota_ref'])
ref

id_punto  prof_diver  quota_ref
0  Pz1_diver          15     146.26
1  Pz2_diver          15     128.68
2  Pz3_diver          15     132.98
3  Pz4_diver          15     128.68

# 1. Manage Eijkelkamp data

In [ ]:
# Write the date set in the folder
# format: AAMMDD
date = '250205'

files = glob.glob(os.path.join(cwd, 'File_originali', 'Eijkelkamp', f'{date}_XLSX', '*.xlsx'))
files
bigdf = um.compute_head_cont(files, ref, saveindf=True, waterlevel=True)

# Rename Pz2 to Pz4 since Pz2 was instead measuring Pz4
bigdf.loc[bigdf.MonitoringPoint == 'Pz2_diver', 'MonitoringPoint'] = 'Pz4_diver'

# Clean the time series from anomalous values
# These values are due to the datalogger movement during measuring campaigns and when it was positioned/removed
# The anomalous values are put equal to the last observed value

clean = [
    ['Pz3_diver', '2024-04-30 16:30:00'],
    ['Pz4_diver', '2024-04-30 16:00:00'],
    ['Pz3_diver', '2024-07-06 11:00:00'],
    ['Pz4_diver', '2024-07-06 11:30:00']
]
for cln in clean:
    idx = bigdf.loc[(bigdf['MonitoringPoint'] == cln[0]) & (bigdf['TimeStamp'] == cln[1])].index
    bigdf.loc[idx, 'quota_falda'] = bigdf.loc[idx-1, 'quota_falda']
    bigdf.loc[idx, 'Temperature'] = bigdf.loc[idx-1, 'Temperature']

# Drop measurements taken after 26/07/2024
bigdf.drop(bigdf.loc[(bigdf['MonitoringPoint'] == 'Pz3_diver') & (bigdf.TimeStamp > '2024-07-26')].index, inplace=True)
bigdf.drop(bigdf.loc[(bigdf['MonitoringPoint'] == 'Pz4_diver') & (bigdf.TimeStamp > '2024-07-26')].index, inplace=True)
bigdf.reset_index(inplace=True, drop=True)

# Export the unified dataframe
bigdf.to_csv(os.path.join(cwd, 'Elaborazioni', 'Eijkelkamp', f'df_Eijk_unificato_{date}.csv'), index = False)

# 2. Manage Keller data

In [5]:
# Define needed parameters

datekeller = '250212'
folders = glob.glob(os.path.join(cwd, 'File_originali', 'KELLER', '**'))

folders = [path for path in folders if 'txt' not in path]
folders = [path for path in folders if 'WWF' not in path]

# calcolo della soggiacenza
B = 15          # installation length [m]
density = 998.2 # [kg/m3], this was the parameter inside LOGGER_5 software
g = 9.80665     # [m/s2]
print('1 cmH20 is equivalent to:')
print(density*g/100, ' [Pa]')
print(density*g/100/100, ' [mbar]')

1 cmH20 is equivalent to:
97.8899803  [Pa]
0.978899803  [mbar]


In [6]:
# Generate a unique df for each measurement point

for i, folder in enumerate(folders):
    ptname = folder.split('\\')[-1]

    if not os.path.exists(os.path.join(cwd, 'Elaborazioni', 'KELLER', ptname, 'merged')):
        os.makedirs(os.path.join(cwd, 'Elaborazioni', 'KELLER', ptname, 'merged'))
    
    files = glob.glob(os.path.join(folder, 'CSV', '*.csv'))
    bigdf = pd.DataFrame()
    for file in files:
        df = um.load_keller_csv(file)
        bigdf = pd.concat([bigdf, df], axis = 0)
    bigdf.sort_values('datetime', inplace=True)
    bigdf.drop_duplicates('datetime', inplace = True)
    bigdf['colonna_h2o'] = bigdf['P1-P2']/(density*g/100/100)/100 # [mH2O]
    if ptname not in ['Fontanile_Nuovo', 'Fontanile_Litta']:
        q = ref.loc[ref.id_punto.str.contains(ptname), 'quota_ref'].values[0]
        bigdf['sogg'] = B - bigdf['colonna_h2o']    # [m]
        bigdf['quota_falda'] = q - bigdf.sogg    # [m.s.l.m.]
    bigdf.to_csv(os.path.join(cwd, 'Elaborazioni', 'KELLER', ptname, 'merged', f"{ptname}_{datekeller}.csv"), index=False)

In [46]:
# Clean the df

# Write the dates that have to cleaned
tobecleaned = {
    'Pz2': [['2024-09-22 14:10:05', '2024-09-22 14:20:05'],
            ['2024-09-25 15:54:05', '2024-09-25 22:30:00'],
            ['2024-10-02 10:30:00', '2024-10-02 13:00:00'],
            ['2024-12-06 13:00:00', '2024-12-06 15:00:00'],
            ['2025-01-09 11:00:00', '2025-01-09 15:00:00'],
            ['2025-01-10 11:00:00', '2025-01-10 14:00:00'],],
    'Pz3': [['2024-09-04 13:46:38', '2024-09-04 15:46:38'],
            ['2024-09-22 15:46:38', '2024-09-22 17:46:38'],
            ['2024-09-25 13:46:38', '2024-09-25 15:46:37'],
            ['2024-12-06 12:46:37', '2024-12-06 14:46:37'],
            ['2024-12-09 12:46:37', '2024-12-09 14:46:37'],
            ['2025-01-09 12:46:37', '2025-01-09 14:46:37'],
            ['2025-01-10 12:46:37', '2025-01-10 14:46:37'],],
    'Pz4': [['2024-09-22 15:59:44', '2024-09-22 17:59:44'],
            ['2024-09-25 12:59:44', '2024-09-25 14:59:43'],
            ['2024-11-10 14:59:43', '2024-11-10 17:59:43'],
            ['2024-12-06 14:59:43', '2024-12-06 16:59:43'],
            ['2025-01-10 12:59:43', '2025-01-10 14:59:43'],],
    'Fontanile_Nuovo': [['2024-12-09 09:24:22', '2024-12-09 16:24:22'],]
}

bigdf = pd.DataFrame()
for folder in folders:
    # Define variables needed
    ptname = folder.split('\\')[-1]
    df = pd.read_csv(os.path.join(cwd, 'Elaborazioni', 'KELLER', ptname, 'merged', f"{ptname}_{datekeller}.csv"))
    # df.datetime = pd.to_datetime(df.datetime, format = '%Y-%m-%d %H:%M:%S')
    out = df.copy()
    out = out.iloc[1:] # rimuovi il primo dato (è errato)

    if ptname in tobecleaned.keys():
        
        for dts in tobecleaned[ptname]:
            out.loc[(out.datetime > dts[0]) & (out.datetime < dts[1]), 'colonna_h2o'] = out.loc[out.datetime == dts[0], 'colonna_h2o'].values[0]
            out.loc[(out.datetime > dts[0]) & (out.datetime < dts[1]), 'TOB1'] = out.loc[out.datetime == dts[0], 'TOB1'].values[0]
            
            if ptname not in ['Fontanile_Nuovo', 'Fontanile_Litta']:
                out.loc[(out.datetime > dts[0]) & (out.datetime < dts[1]), 'quota_falda'] = out.loc[out.datetime == dts[0], 'quota_falda'].values[0]
                #correggi i valori dalla seconda data in avanti
                delta = df.loc[df.datetime == dts[1],'quota_falda'].values[0] - df.loc[df.datetime == dts[0],'quota_falda'].values[0]
                out.loc[out.datetime >= dts[1], 'quota_falda'] = out.loc[out.datetime >= dts[1], 'quota_falda'] - delta
            
            delta = df.loc[df.datetime == dts[1],'TOB1'].values[0] - df.loc[df.datetime == dts[0],'TOB1'].values[0]
            out.loc[out.datetime >= dts[1], 'TOB1'] = out.loc[out.datetime >= dts[1], 'TOB1'] - delta

            delta = df.loc[df.datetime == dts[1], 'colonna_h2o'].values[0] - df.loc[df.datetime == dts[0], 'colonna_h2o'].values[0]
            out.loc[out.datetime >= dts[1], 'colonna_h2o'] = out.loc[out.datetime >= dts[1], 'colonna_h2o'] - delta
            
        if ptname not in ['Fontanile_Nuovo', 'Fontanile_Litta']:
            quota = ref.loc[ref.id_punto.str.contains(ptname), 'quota_ref'].values[0]
            out.sogg = quota - out.quota_falda
        
        out.to_csv(os.path.join(cwd, 'Elaborazioni', 'KELLER', ptname, 'merged', f'{ptname}_{datekeller}_cleaned.csv'))
    
    # Merge into a unique dataframe
    out['id_punto'] = f'{ptname}_diver'
    bigdf = pd.concat([bigdf, out], axis=0)

bigdf.to_csv(os.path.join(cwd, 'Elaborazioni', 'KELLER', f'df_Kell_unificato_{datekeller}.csv'), index = False)

## 2.2. Visualize the dataframe

In [47]:
df = pd.read_csv(os.path.join(cwd, 'Elaborazioni', 'KELLER', f'df_Kell_unificato_{datekeller}.csv'))
df.head()

Date      Time   P1-P2        P1        P2   TOB1  TOB2  \
0  2025-02-06  11:00:00  19.090  1036.621  1017.548  13.87  2.40   
1  2025-02-06  12:00:00  19.051  1036.163  1017.120  14.36  4.28   
2  2025-02-06  13:00:00  19.350  1035.645  1016.296  14.79  6.75   
3  2025-02-06  14:00:00  19.419  1034.821  1015.411  14.87  8.17   
4  2025-02-06  15:00:00  19.426  1034.210  1014.771  14.79  8.63   

              datetime  colonna_h2o               id_punto  sogg  quota_falda  
0  2025-02-06 11:00:00     0.195015  Fontanile_Litta_diver   NaN          NaN  
1  2025-02-06 12:00:00     0.194616  Fontanile_Litta_diver   NaN          NaN  
2  2025-02-06 13:00:00     0.197671  Fontanile_Litta_diver   NaN          NaN  
3  2025-02-06 14:00:00     0.198376  Fontanile_Litta_diver   NaN          NaN  
4  2025-02-06 15:00:00     0.198447  Fontanile_Litta_diver   NaN          NaN

In [48]:
um.interactive_TS_visualization(df.pivot_table(index='datetime', values='colonna_h2o', columns='id_punto'), ret = True, markers=True)

### 2.2.1. Visualize single series

In [41]:
ptname = 'Pz2'
df = pd.read_csv(os.path.join(cwd, 'Elaborazioni', 'KELLER', f'{ptname}', 'merged', f'{ptname}_{datekeller}.csv'))

In [42]:
um.interactive_TS_visualization(df.set_index('datetime')['colonna_h2o'], ret = True, markers=True)

# 3. Manage OTT data

# 4. Merge the data in a unique dataframe

In [ ]:
# Eijkelkamp
os.path.join(cwd, 'Elaborazioni', 'Eijkelkamp', f'df_Eijk_unificato_{date}.csv')
# Keller
pd.read_csv(os.path.join(cwd, 'Elaborazioni', 'KELLER', f'df_Kell_unificato_{datekeller}.csv'))
# OTT
